# CGC SDK

In this tutorial you will shown how to connect with databases in your namespace.

## Requirements

We have included module in `cgcsdk` that wraps common tools to interact with different databases.

Install it by running:



In [1]:
!pip install cgcsdk

  Using cached cgcsdk-0.8.5-py3-none-any.whl (62 kB)

[notice] A new release of pip is available: 23.1 -> 23.1.2
[notice] To update, run: python -m pip install --upgrade pip


## Import SDK

After successful installation, import our sdk

In [1]:
import cgc.sdk as sdk

## MongoDB

For Mongo our wrapper is enhanced with useful commands to interact with DB.
Firstly we create connection to DB with:

- name of running Mongo instance
- token generated for that instance

In [2]:
mongo = sdk.mongo_client("mongo","aed0bf3d8e8545daa667d230ff5c04a9")

authSource=admin&readPreference=primaryPreferred&ssl=false
Connected to MongoDB (db): mongo:27017


Now we can insert data to database named by default **db** with `insert_one` function

In [3]:
curr = mongo.insert_one("test",query={
                "name": "bob"})

To get data from our db, simply run `find` command to retrieve mongo cursor with data

In [4]:
curr = mongo.find("test",{})

Print data from our cursor

In [5]:
for c in curr:
    print(c)

{'_id': ObjectId('643e7691000dea69ca7c18b5'), 'name': 'bob'}
{'_id': ObjectId('643e7b29be531069384670e9'), 'name': 'bob'}
{'_id': ObjectId('645cd776a56ed8653d33c536'), 'name': 'bob'}
{'_id': ObjectId('645cd8c68bec6c21816c3d89'), 'name': 'bob'}


Cursor is from `pymongo`, so you can use same methods as with
that cursor.

ex. `curr.next()`


If want to use connector from `pymongo`, use following commands to retrieve it and do same stuff as shown above:


In [6]:
mongo_client = mongo.get_pymongo_client()
db = mongo_client['db']
collection = db['test']
mongo_data = collection.find({})
for m in mongo_data:
    print(m)

{'_id': ObjectId('643e7691000dea69ca7c18b5'), 'name': 'bob'}
{'_id': ObjectId('643e7b29be531069384670e9'), 'name': 'bob'}
{'_id': ObjectId('645cd776a56ed8653d33c536'), 'name': 'bob'}
{'_id': ObjectId('645cd8c68bec6c21816c3d89'), 'name': 'bob'}


## Redis

Similarly to Mongo, use Redis instance name and token to connect

In [7]:
redis = sdk.redis_client("redis", "19ac9da50b124e38bbdea8a7e5d86252")

Connected to Redis: redis


Retrieve Redis object which is from `redis` package.

In [8]:
redis_client = redis.get_redis_client()

Interact with database

In [9]:
redis_client.set('foo', 'bar')
value = redis_client.get('foo')
print(value)

b'bar'


## PostgreSQL

For PostgreSQL we have only wrapper that connects with database.

Use PostgreSQL instance name and token to connect

In [10]:
postgresql = sdk.postgresql_client("postgresql","fec387f993934ccebe4d24ef2f079720")

Connected to PostgreSQL (db): postgresql


Retrieve PostgreSQL object which is from `psycopg2` package.

In [11]:
postgresql_client = postgresql.get_postgresql_client()

from `psycopg2` import `sql` to create easily in Python SQL queries.


In [12]:
from psycopg2 import sql

cursor = postgresql_client.cursor()

If not created, create Table with following code:

In [13]:
sql_command = sql.SQL('''
CREATE TABLE Customer 
(CustomerID INT PRIMARY KEY NOT NULL,
CustomerName VARCHAR(50),
LastName VARCHAR(50),
Country VARCHAR(50),
Age INT,
Phone INT
);
''')
cursor.execute(sql_command)

DuplicateTable: relation "customer" already exists


Add some data to database:

In [13]:
sql_command = sql.SQL('''
INSERT INTO Customer 
(CustomerID,
CustomerName,
LastName,
Country,
Age,
Phone) VALUES (%s,%s,%s,%s,%s,%s)
''')
record_to_insert = (3, 'Zbigniew', "Polak", "Bali", 69, 991991991)
cursor.execute(sql_command,record_to_insert)
postgresql_client.commit()

To display data from Table, you could execute `SELECT` query:

In [14]:
cursor = postgresql_client.cursor()
cursor.execute("SELECT * FROM Customer")
cursor.fetchall()

[(1, 'Zbigniew', 'Marchewa', 'Cuba', 69, 991991991),
 (2, 'Zbigniew', 'Marchewa', 'Cuba', 69, 991991991),
 (3, 'Zbigniew', 'Polak', 'Bali', 69, 991991991)]

If you want to connect to this SQL database without our wrapper, simply use following code example:

In [ ]:
import psycopg2

client = psycopg2.connect(
                    database="db",
                    host="postgresql",
                    user="admin",
                    password="fec387f993934ccebe4d24ef2f079720",
                )
cursor = client.cursor()

cursor.execute("SELECT * FROM Customer")
cursor.fetchall()
